In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:90% !important; }</style>"))


import matplotlib.pyplot as plt
import matplotlib.patheffects as pe
import os
import pandas as pd
import seaborn as sb
import statistics as st

from Bio import SeqIO

sb.set()
pd.set_option("display.max_rows", None)

# Evaluation of USEARCH and VSEARCH on Franzén data

The following notebook describes the steps and results of the evaluation.

In [ ]:
# Initial files and directories:
#
# uvsearch_franzen
# |- data # will contain the in-silico sequenced data sets
# |
# |- evaluation # will contain the evaluation plots and tables
# |
# |- outputs # will contain the cluster and metric outputs
# |
# |- tasks  # task files for the different runs of U/VSEARCH
# |
# \- 40168_2015_105_MOESM9_ESM.csv  # CSV version of Additional file 9 of Franzén et al. (see below)

## Analysis workflow

The data sets are prepared as described in Franzén et al., *Improved OTU-picking using long-read 16S rRNA gene amplicon sequencing and generic hierarchical clustering* (https://doi.org/10.1186/s40168-015-0105-6),
except that there are no Ns between the forward and reverse portion of the reads.

The taxonomic assignment is obtained from the known sources during the creation of the mock communities (simulated sequencing).

Both tools are run with several clustering options:
 - USEARCH: `-cluster_fast`, `-cluster_smallmem`
 - VSEARCH: `--cluster_fast`, `--cluster_size`, `--cluster_smallmem`

## Commands

The following commands prepare and cluster the data sets. The results are evaluated below.

In order to execute the workflow as provided here, the `tools` subdirectory of the overall repository has to contain the binaries of Infernal (cmbuild, cmalign) and ART (art_illumina),
a VSEARCH binary and the USEARCH binary `usearch11.0.667_i86linux32`, but the paths can be adjusted. 

IMPORTANT: The commands are not intended to be executed from this notebook. They should be executed from the root directory of the overall repository.

In [ ]:
%%bash

TOOLS_DIR=tools
ANALYSIS_DIR=analyses/uvsearch_franzen
DATA_DIR=${ANALYSIS_DIR}/data
OUTPUT_DIR=${ANALYSIS_DIR}/outputs

USEARCH=${TOOLS_DIR}/usearch11.0.667_i86linux32 # adjust to your system
VSEARCH=${TOOLS_DIR}/vsearch-2.14.2-linux-x86_64/bin/vsearch # adjust to your system

RUNS=( usearch_fast_length usearch_fast_size usearch_smallmem_length usearch_smallmem_size vsearch_fast vsearch_size vsearch_smallmem_length vsearch_smallmem_size )

# prepare tools and reference data
CMBUILD_PATH=${TOOLS_DIR}/infernal-1.1.2-linux-intel-gcc/binaries/cmbuild # adjust to your system
python -m scripts.analyses.analysis_franzen prepare ${DATA_DIR} --cmbuild ${CMBUILD_PATH}

# create list files of mock communities
python -m scripts.analyses.analysis_franzen lists ${ANALYSIS_DIR}/40168_2015_105_MOESM9_ESM.csv ${DATA_DIR}/list_files

# create mock communities
GG_DB=${DATA_DIR}/gg_13_5.fasta
MOCK_LIST=${DATA_DIR}/list_files/list.txt
MSA_MODEL=${DATA_DIR}/bacteria16S_508_mod5.cmfile
CMALIGN_PATH=${TOOLS_DIR}/infernal-1.1.2-linux-intel-gcc/binaries/cmalign # adjust to your system
ART_PATH=${TOOLS_DIR}/art_bin_VanillaIceCream/art_illumina # adjust to your system
python -m scripts.analyses.analysis_franzen mock ${GG_DB} ${MOCK_LIST} ${MSA_MODEL} ${DATA_DIR} --cmalign ${CMALIGN_PATH} --art ${ART_PATH} --miseq --skip_ambiguous --num_n 0

# run U/VSEARCH an determine clustering quality
DATA=( "LC" "MC" "HC" )
REGIONS=( "V3-V4" "V4" )
for D in "${DATA[@]}"; do
  for ((I=1; I<=10; I++)); do
    for R in "${REGIONS[@]}"; do
      echo ${D}_${I}_${R}
      READS=${D}_${I}_${R}:${DATA_DIR}/${D}_${I}/${D}_${I}_${R}_miseq_rs.fastq
      TAX=franzen:${DATA_DIR}/${D}_${I}/${D}_${I}_${R}_miseq_rs.tax
      for RUN in "${RUNS[@]}"; do
        python -m scripts.analyses.analysis_franzen run_uvsearch ${RUN} ${READS} ${ANALYSIS_DIR}/tasks/${RUN}.txt ${OUTPUT_DIR}/${D}_${I}_${R}/${RUN} --tax_files ${TAX} --usearch ${USEARCH} --vsearch ${VSEARCH}
        for F in ${OUTPUT_DIR}/${D}_${I}_${R}/${RUN}/*__metrics.csv; do mv ${F} ${OUTPUT_DIR}/${D}_${I}_${R}/${RUN}/${RUN}_${F##*/}; done
      done
    done
  done
done

## Evaluation

**Configuration**

In [2]:
data_sets = ['LC', 'MC', 'HC']
num_samples = 10
regions = ['V3-V4', 'V4']
ground_truths = ['franzen']

opts = ['usearch_fast_length', 'usearch_fast_size', 'usearch_smallmem_length', 'usearch_smallmem_size', 'vsearch_fast', 'vsearch_size', 'vsearch_smallmem_length', 'vsearch_smallmem_size']

data_dir = 'data'
results_dir = 'outputs'
eval_dir = 'evaluation'

### Number of clusters and amplicons

Reads the input files and the cluster outputs for all data sets and compares the number of clusters and amplicons.

In [3]:
# Requires the input and OTU files. Alternatively, the evaluation can use the stored information (see below).
df_columns = ['data_set', 'tool', 'mode', 'refinement', 'threshold', 'num_input_amplicons', 'input_mass', 'num_clusters', 'num_output_amplicons', 'output_mass', 'ds', 'rt']

rows = []

for ds in data_sets:
    for rt in regions:
        for s in range(1, num_samples + 1):
            run_name = '%s_%i_%s' % (ds, s, rt)
            
            seq_file = '%s/%s_%i/%s_miseq_rs.fastq' % (data_dir, ds, s, run_name) # the input sequences
            num_input_amplicons = 0
            input_mass = 0
            with open(seq_file, 'r') as in_file:
                for record in SeqIO.parse(in_file, 'fastq'):
                    num_input_amplicons += 1
                    input_mass += int(record.id.split('_')[-1]) if ('_' in record.id) else 1
            
            for opt in opts:                
                otu_files = [f for f in os.listdir('%s/%s/%s/' % (results_dir, run_name, opt)) if f.endswith('_otus.txt')]

                for f in otu_files:
                    otu_file = '%s/%s/%s/%s' % (results_dir, run_name, opt, f)

                    num_output_amplicons = 0
                    num_clusters = 0
                    output_mass = 0
                    with open(otu_file, 'r') as in_file:
                        for line in in_file:
                            num_output_amplicons += len(line.strip().split(' '))
                            num_clusters += 1
                            output_mass += sum([int(m.split('_')[-1]) for m in line.strip().split(' ')])
                            
                    tool, mode = f.split('__')
                    mode = mode.split('_0')[0]
                    refinement = 'nf'
                    threshold = float(f.split('_')[-2])

                    rows.append([run_name, tool, mode, refinement, threshold, num_input_amplicons, input_mass, num_clusters, num_output_amplicons, output_mass, ds, rt])
            
df_counts = pd.DataFrame(rows, columns = df_columns)

*Column descriptions:*   
`num_input_amplicons`: The number of entries in the corresponding input file.   
`input_mass`: The sum of the abundances of all entries in the input file.   
`num_clusters`: The number of computed clusters.   
`num_output_amplicons`: The number of amplicons contained in the clusters.   
`output_mass`: The sum of the abundances of all amplicons contained in the clusters.   

In [4]:
df_counts[['data_set', 'tool', 'mode', 'threshold', 'num_input_amplicons', 'input_mass', 'num_clusters', 'num_output_amplicons', 'output_mass']]

data_set     tool             mode  threshold  num_input_amplicons  \
0      LC_1_V3-V4  usearch      fast_length       0.90                 1980   
1      LC_1_V3-V4  usearch      fast_length       0.91                 1980   
2      LC_1_V3-V4  usearch      fast_length       0.92                 1980   
3      LC_1_V3-V4  usearch      fast_length       0.93                 1980   
4      LC_1_V3-V4  usearch      fast_length       0.94                 1980   
5      LC_1_V3-V4  usearch      fast_length       0.95                 1980   
6      LC_1_V3-V4  usearch      fast_length       0.96                 1980   
7      LC_1_V3-V4  usearch      fast_length       0.97                 1980   
8      LC_1_V3-V4  usearch      fast_length       0.98                 1980   
9      LC_1_V3-V4  usearch      fast_length       0.99                 1980   
10     LC_1_V3-V4  usearch        fast_size       0.90                 1980   
11     LC_1_V3-V4  usearch        fast_size       0.91                 1980   
12     LC_1_V3-V4  usearch        fast_size       0.92                 1980   
13     LC_1_V3-V4  usearch        fast_size       0.93                 1980   
14     LC_1_V3-V4  usearch        fast_size       0.94                 1980   
15     LC_1_V3-V4  usearch        fast_size       0.95                 1980   
16     LC_1_V3-V4  usearch        fast_size       0.96                 1980   
17     LC_1_V3-V4  usearch        fast_size       0.97                 1980   
18     LC_1_V3-V4  usearch        fast_size       0.98                 1980   
19     LC_1_V3-V4  usearch        fast_size       0.99                 1980   
20     LC_1_V3-V4  usearch  smallmem_length       0.90                 1980   
21     LC_1_V3-V4  usearch  smallmem_length       0.91                 1980   
22     LC_1_V3-V4  usearch  smallmem_length       0.92                 1980   
23     LC_1_V3-V4  usearch  smallmem_length       0.93                 1980   
24     LC_1_V3-V4  usearch  smallmem_length       0.94                 1980   
25     LC_1_V3-V4  usearch  smallmem_length       0.95                 1980   
26     LC_1_V3-V4  usearch  smallmem_length       0.96                 1980   
27     LC_1_V3-V4  usearch  smallmem_length       0.97                 1980   
28     LC_1_V3-V4  usearch  smallmem_length       0.98                 1980   
29     LC_1_V3-V4  usearch  smallmem_length       0.99                 1980   
30     LC_1_V3-V4  usearch    smallmem_size       0.90                 1980   
31     LC_1_V3-V4  usearch    smallmem_size       0.91                 1980   
32     LC_1_V3-V4  usearch    smallmem_size       0.92                 1980   
33     LC_1_V3-V4  usearch    smallmem_size       0.93                 1980   
34     LC_1_V3-V4  usearch    smallmem_size       0.94                 1980   
35     LC_1_V3-V4  usearch    smallmem_size       0.95                 1980   
36     LC_1_V3-V4  usearch    smallmem_size       0.96                 1980   
37     LC_1_V3-V4  usearch    smallmem_size       0.97                 1980   
38     LC_1_V3-V4  usearch    smallmem_size       0.98                 1980   
39     LC_1_V3-V4  usearch    smallmem_size       0.99                 1980   
40     LC_1_V3-V4  vsearch             fast       0.90                 1980   
41     LC_1_V3-V4  vsearch             fast       0.91                 1980   
42     LC_1_V3-V4  vsearch             fast       0.92                 1980   
43     LC_1_V3-V4  vsearch             fast       0.93                 1980   
44     LC_1_V3-V4  vsearch             fast       0.94                 1980   
45     LC_1_V3-V4  vsearch             fast       0.95                 1980   
46     LC_1_V3-V4  vsearch             fast       0.96                 1980   
47     LC_1_V3-V4  vsearch             fast       0.97                 1980   
48     LC_1_V3-V4  vsearch             fast       0.98                 1980   
49     LC_1_V3-V4  vsearch             fast       0.99     

In [5]:
df_counts.to_csv('%s/df_counts.csv' % eval_dir, sep = ';', index = False)
#df_counts = pd.read_csv('%s/df_counts.csv' % eval_dir, sep = ';')

### Clustering quality

In [6]:
# Requires the metrics files. Alternatively, the evaluation can use the stored information (see below).
dfs = []
for ds in data_sets:
    for rt in regions:
        for s in range(1, num_samples + 1):
            run_name = '%s_%i_%s' % (ds, s, rt)
            
            for opt in opts:
                for gt in ground_truths:
                    df = pd.read_csv('%s/%s/%s/%s_%s_%s__metrics.csv' % (results_dir, run_name, opt, opt, run_name, gt), sep = ';')
                    
                    df['gt'] = gt
                    df['mode'] = [m.split('__')[-1] for m in df['task']]
                    df['refinement'] = 'nf'
                    df['ds'] = ds
                    df['rt'] = rt
                    
                    dfs.append(df)
                    
df_quality = pd.concat(dfs, ignore_index = True)
df_quality.rename(columns = {'task': 'run', 'reads': 'data_set'}, inplace = True)

*Column descriptions:*   
`precision`: Quantifies the extent to which amplicons in a cluster are also from the same species.   
`recall`: Measures the proportion of amplicons from the same species that are grouped in the same cluster.   
`adjrandindex`: Measures the agreement between the clusters and the taxonomic assignment and corrects for chance.   

In [7]:
df_quality[['data_set', 'gt', 'tool', 'mode', 'threshold', 'precision', 'recall', 'adjrandindex']]

data_set       gt     tool             mode  threshold  precision  \
0      LC_1_V3-V4  franzen  usearch      fast_length       0.90   0.621021   
1      LC_1_V3-V4  franzen  usearch      fast_length       0.91   0.668519   
2      LC_1_V3-V4  franzen  usearch      fast_length       0.92   0.730167   
3      LC_1_V3-V4  franzen  usearch      fast_length       0.93   0.764528   
4      LC_1_V3-V4  franzen  usearch      fast_length       0.94   0.787772   
5      LC_1_V3-V4  franzen  usearch      fast_length       0.95   0.829207   
6      LC_1_V3-V4  franzen  usearch      fast_length       0.96   0.879737   
7      LC_1_V3-V4  franzen  usearch      fast_length       0.97   0.936331   
8      LC_1_V3-V4  franzen  usearch      fast_length       0.98   0.971198   
9      LC_1_V3-V4  franzen  usearch      fast_length       0.99   0.997979   
10     LC_1_V3-V4  franzen  usearch        fast_size       0.90   0.624053   
11     LC_1_V3-V4  franzen  usearch        fast_size       0.91   0.665993   
12     LC_1_V3-V4  franzen  usearch        fast_size       0.92   0.728146   
13     LC_1_V3-V4  franzen  usearch        fast_size       0.93   0.765538   
14     LC_1_V3-V4  franzen  usearch        fast_size       0.94   0.787772   
15     LC_1_V3-V4  franzen  usearch        fast_size       0.95   0.829712   
16     LC_1_V3-V4  franzen  usearch        fast_size       0.96   0.880748   
17     LC_1_V3-V4  franzen  usearch        fast_size       0.97   0.937847   
18     LC_1_V3-V4  franzen  usearch        fast_size       0.98   0.971198   
19     LC_1_V3-V4  franzen  usearch        fast_size       0.99   0.997979   
20     LC_1_V3-V4  franzen  usearch  smallmem_length       0.90   0.609904   
21     LC_1_V3-V4  franzen  usearch  smallmem_length       0.91   0.679131   
22     LC_1_V3-V4  franzen  usearch  smallmem_length       0.92   0.730672   
23     LC_1_V3-V4  franzen  usearch  smallmem_length       0.93   0.775139   
24     LC_1_V3-V4  franzen  usearch  smallmem_length       0.94   0.778171   
25     LC_1_V3-V4  franzen  usearch  smallmem_length       0.95   0.817079   
26     LC_1_V3-V4  franzen  usearch  smallmem_length       0.96   0.879737   
27     LC_1_V3-V4  franzen  usearch  smallmem_length       0.97   0.945932   
28     LC_1_V3-V4  franzen  usearch  smallmem_length       0.98   0.971198   
29     LC_1_V3-V4  franzen  usearch  smallmem_length       0.99   0.997473   
30     LC_1_V3-V4  franzen  usearch    smallmem_size       0.90   0.609904   
31     LC_1_V3-V4  franzen  usearch    smallmem_size       0.91   0.679131   
32     LC_1_V3-V4  franzen  usearch    smallmem_size       0.92   0.730672   
33     LC_1_V3-V4  franzen  usearch    smallmem_size       0.93   0.775139   
34     LC_1_V3-V4  franzen  usearch    smallmem_size       0.94   0.778171   
35     LC_1_V3-V4  franzen  usearch    smallmem_size       0.95   0.817079   
36     LC_1_V3-V4  franzen  usearch    smallmem_size       0.96   0.879737   
37     LC_1_V3-V4  franzen  usearch    smallmem_size       0.97   0.945932   
38     LC_1_V3-V4  franzen  usearch    smallmem_size       0.98   0.971198   
39     LC_1_V3-V4  franzen  usearch    smallmem_size       0.99   0.997473   
40     LC_1_V3-V4  franzen  vsearch             fast       0.90   0.609904   
41     LC_1_V3-V4  franzen  vsearch             fast       0.91   0.658919   
42     LC_1_V3-V4  franzen  vsearch             fast       0.92   0.713997   
43     LC_1_V3-V4  franzen  vsearch             fast       0.93   0.774634   
44     LC_1_V3-V4  franzen  vsearch             fast       0.94   0.784740   
45     LC_1_V3-V4  franzen  vsearch             fast       0.95   0.823143   
46     LC_1_V3-V4  franzen  vsearch             fast       0.96   0.902476   
47     LC_1_V3-V4  franzen  vsearch             fast       0.97   0.954522   
48     LC_1_V3-V4  franzen  vsearch             fast       0.98   0.973724   
49     LC_1_V3-V4  franzen  vsearch             fast       0.99   0.997979   
50     LC_1_V3-V4  franzen  vse

In [8]:
df_quality.to_csv('%s/df_quality.csv' % eval_dir, sep = ';', index = False)
#df_quality = pd.read_csv('%s/df_quality.csv' % eval_dir, sep = ';')

Combine counting and quality information:

In [9]:
df_c, df_q = df_counts.copy(), df_quality.copy()
drop_cols = ['join_col'] + ['%s_counts' % s for s in set(df_q.columns) & set(df_c.columns)]
df_c['join_col'] = df_c['data_set'] + df_c['tool'] + df_c['mode'] + df_c['refinement'] + df_c['threshold'].apply(str)
df_q['join_col'] = df_q['data_set'] + df_q['tool'] + df_q['mode'] + df_q['refinement'] + df_q['threshold'].apply(str)
df_joined = df_q.join(df_c.set_index('join_col'), on = 'join_col', rsuffix = '_counts').drop(drop_cols, axis = 1)

In [10]:
df_joined.to_csv('%s/df_joined.csv' % eval_dir, sep = ';', index = False)
#df_joined = pd.read_csv('%s/df_joined.csv' % eval_dir, sep = ';')

Determine the maximum, average and N-best average clustering quality (for N = 5).

In [11]:
df_columns = ['data_set', 'gt', 'tool', 'mode', 'refinement', 'precision', 'recall', 'adjrandindex', 'num_input_amplicons', 'input_mass', 'num_clusters', 'num_output_amplicons', 'output_mass', 'ds', 'rt']

max_rows = []
mean_rows = []
nbest_rows = []
n = 5

for (d, g, t, m, f, ds, rt), grp in df_joined.groupby(by = ['data_set', 'gt', 'tool', 'mode', 'refinement', 'ds', 'rt']):
    best = grp.nlargest(1, 'adjrandindex')
    max_rows.append([d, g, t, m, f, best['precision'].values[0], best['recall'].values[0], best['adjrandindex'].values[0], best['num_input_amplicons'].values[0], best['input_mass'].values[0], best['num_clusters'].values[0], best['num_output_amplicons'].values[0], best['output_mass'].values[0], ds, rt])
    mean_rows.append([d, g, t, m, f, grp['precision'].mean(), grp['recall'].mean(), grp['adjrandindex'].mean(), grp['num_input_amplicons'].mean(), grp['input_mass'].mean(), grp['num_clusters'].mean(), grp['num_output_amplicons'].mean(), grp['output_mass'].mean(), ds, rt])
    nbest = grp.nlargest(n, 'adjrandindex')
    nbest_rows.append([d, g, t, m, f, nbest['precision'].mean(), nbest['recall'].mean(), nbest['adjrandindex'].mean(), nbest['num_input_amplicons'].mean(), nbest['input_mass'].mean(), nbest['num_clusters'].mean(), nbest['num_output_amplicons'].mean(), nbest['output_mass'].mean(), ds, rt])
    
df_joined_max = pd.DataFrame(max_rows, columns = df_columns)
df_joined_mean = pd.DataFrame(mean_rows, columns = df_columns)
df_joined_nbest = pd.DataFrame(nbest_rows, columns = df_columns)

In [12]:
df_joined_max.to_csv('%s/df_joined_max.csv' % eval_dir, sep = ';', index = False)
df_joined_mean.to_csv('%s/df_joined_mean.csv' % eval_dir, sep = ';', index = False)
df_joined_nbest.to_csv('%s/df_joined_nbest.csv' % eval_dir, sep = ';', index = False)
#df_joined_max = pd.read_csv('%s/df_joined_max.csv' % eval_dir, sep = ';')
#df_joined_mean = pd.read_csv('%s/df_joined_mean.csv' % eval_dir, sep = ';')
#df_joined_nbest = pd.read_csv('%s/df_joined_nbest.csv' % eval_dir, sep = ';')

In [13]:
df_max = df_joined_max.loc[df_joined_max['gt'] == 'franzen']
df_mean = df_joined_mean.loc[df_joined_mean['gt'] == 'franzen']
df_nbest = df_joined_nbest.loc[df_joined_nbest['gt'] == 'franzen']

For the chosen ground truth, average the maximum, average and N-best average values per complexity (e.g. LC) and read type (e.g. V3-V4).   

In [14]:
df_columns = ['data_set', 'gt', 'tool', 'mode', 'refinement', 'precision', 'recall', 'adjrandindex', 'num_input_amplicons', 'input_mass', 'num_clusters', 'num_output_amplicons', 'output_mass', 'ds', 'rt']

def average_complexity(df):
    rows = []
    for (gt, ds, rt, tool, mode, f), grp in df.groupby(by = ['gt', 'ds', 'rt', 'tool', 'mode', 'refinement']):
        rows.append(['%s_%s' % (ds, rt), gt, tool, mode, f, grp['precision'].mean(), grp['recall'].mean(), grp['adjrandindex'].mean(), grp['num_input_amplicons'].mean(), grp['input_mass'].mean(), grp['num_clusters'].mean(), grp['num_output_amplicons'].mean(), grp['output_mass'].mean(), ds, rt])
    return pd.DataFrame(rows, columns = df_columns)

In [15]:
df_joined_max_avg = average_complexity(df_max)
df_joined_mean_avg = average_complexity(df_mean)
df_joined_nbest_avg = average_complexity(df_nbest)

In [16]:
df_joined_max_avg.to_csv('%s/df_joined_max_avg.csv' % eval_dir, sep = ';', index = False)
df_joined_mean_avg.to_csv('%s/df_joined_mean_avg.csv' % eval_dir, sep = ';', index = False)
df_joined_nbest_avg.to_csv('%s/df_joined_nbest_avg.csv' % eval_dir, sep = ';', index = False)
#df_joined_max_avg = pd.read_csv('%s/df_joined_max_avg.csv' % eval_dir, sep = ';')
#df_joined_mean_avg = pd.read_csv('%s/df_joined_mean_avg.csv' % eval_dir, sep = ';')
#df_joined_nbest_avg = pd.read_csv('%s/df_joined_nbest_avg.csv' % eval_dir, sep = ';')

**Maximum clustering quality**

Rank by adjusted Rand index (per data set):

In [17]:
for (d, t), grp in df_joined_max_avg.groupby(by = ['data_set', 'tool']):
    print('Data set: %s / Tool: %s' % (d, t))
    display(grp.sort_values(by = 'adjrandindex', ascending = False))

Data set: HC_V3-V4 / Tool: usearch


data_set       gt     tool             mode refinement  precision  \
0  HC_V3-V4  franzen  usearch      fast_length         nf   0.791259   
2  HC_V3-V4  franzen  usearch  smallmem_length         nf   0.789708   
3  HC_V3-V4  franzen  usearch    smallmem_size         nf   0.789708   
1  HC_V3-V4  franzen  usearch        fast_size         nf   0.789497   

     recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
0  0.890521      0.634581               9958.0      9958.0         706.1   
2  0.897318      0.623739               9958.0      9958.0         669.3   
3  0.897318      0.623739               9958.0      9958.0         669.3   
1  0.889525      0.618244               9958.0      9958.0         712.0   

   num_output_amplicons  output_mass  ds     rt  
0                9952.4       9958.0  HC  V3-V4  
2                9952.4       9958.0  HC  V3-V4  
3                9952.4       9958.0  HC  V3-V4  
1                9952.4       9958.0  HC  V3-V4

Data set: HC_V3-V4 / Tool: vsearch


data_set       gt     tool             mode refinement  precision  \
4  HC_V3-V4  franzen  vsearch             fast         nf   0.811487   
5  HC_V3-V4  franzen  vsearch             size         nf   0.811477   
6  HC_V3-V4  franzen  vsearch  smallmem_length         nf   0.811477   
7  HC_V3-V4  franzen  vsearch    smallmem_size         nf   0.811477   

     recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
4  0.924978      0.655363               9958.0      9958.0         668.3   
5  0.924978      0.655353               9958.0      9958.0         668.2   
6  0.924978      0.655353               9958.0      9958.0         668.2   
7  0.924978      0.655353               9958.0      9958.0         668.2   

   num_output_amplicons  output_mass  ds     rt  
4                9952.4       9958.0  HC  V3-V4  
5                9952.4       9958.0  HC  V3-V4  
6                9952.4       9958.0  HC  V3-V4  
7                9952.4       9958.0  HC  V3-V4

Data set: HC_V4 / Tool: usearch


...

data_set       gt     tool             mode refinement  precision  \
36  MC_V3-V4  franzen  vsearch             fast         nf   0.873321   
37  MC_V3-V4  franzen  vsearch             size         nf   0.873321   
38  MC_V3-V4  franzen  vsearch  smallmem_length         nf   0.873321   
39  MC_V3-V4  franzen  vsearch    smallmem_size         nf   0.873321   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
36  0.937516      0.790458               4966.0      4966.0         335.1   
37  0.937516      0.790458               4966.0      4966.0         335.1   
38  0.937516      0.790458               4966.0      4966.0         335.1   
39  0.937516      0.790458               4966.0      4966.0         335.1   

    num_output_amplicons  output_mass  ds     rt  
36                4962.6       4966.0  MC  V3-V4  
37                4962.6       4966.0  MC  V3-V4  
38                4962.6       4966.0  MC  V3-V4  
39                4962.6       4966.0  MC  V3-V4

Data set: MC_V4 / Tool: usearch


data_set       gt     tool             mode refinement  precision  \
40    MC_V4  franzen  usearch      fast_length         nf   0.835802   
41    MC_V4  franzen  usearch        fast_size         nf   0.836071   
42    MC_V4  franzen  usearch  smallmem_length         nf   0.844354   
43    MC_V4  franzen  usearch    smallmem_size         nf   0.844354   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
40  0.923611      0.737577               4966.0      4966.0         334.8   
41  0.907750      0.706774               4966.0      4966.0         535.3   
42  0.897491      0.705809               4966.0      4966.0         580.7   
43  0.897491      0.705809               4966.0      4966.0         580.7   

    num_output_amplicons  output_mass  ds  rt  
40                4101.5       4966.0  MC  V4  
41                4101.5       4966.0  MC  V4  
42                4101.5       4966.0  MC  V4  
43                4101.5       4966.0  MC  V4

Data set: MC_V4 / Tool: vsearch


data_set       gt     tool             mode refinement  precision  \
44    MC_V4  franzen  vsearch             fast         nf   0.839025   
45    MC_V4  franzen  vsearch             size         nf   0.839025   
46    MC_V4  franzen  vsearch  smallmem_length         nf   0.839025   
47    MC_V4  franzen  vsearch    smallmem_size         nf   0.839025   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
44  0.907263      0.707587               4966.0      4966.0         531.5   
45  0.907263      0.707587               4966.0      4966.0         531.5   
46  0.907263      0.707587               4966.0      4966.0         531.5   
47  0.907263      0.707587               4966.0      4966.0         531.5   

    num_output_amplicons  output_mass  ds  rt  
44                4101.5       4966.0  MC  V4  
45                4101.5       4966.0  MC  V4  
46                4101.5       4966.0  MC  V4  
47                4101.5       4966.0  MC  V4

Best option of VSEARCH better than best option of USEARCH on each V3-V4 data set and vice versa for V4 data sets.

Average maximum values over all data sets and sort by adjusted Rand index:

In [18]:
rows = []
for (t, m, f), grp in df_joined_max_avg.groupby(by = ['tool', 'mode', 'refinement']):
    rows.append([t, m, f, grp['precision'].mean(), grp['recall'].mean(), grp['adjrandindex'].mean()])
pd.DataFrame(rows, columns = ['tool', 'mode', 'refinement', 'precision', 'recall', 'adjrandindex']).sort_values(by = 'adjrandindex', ascending = False)

tool             mode refinement  precision    recall  adjrandindex
0  usearch      fast_length         nf   0.841591  0.918669      0.732579
4  vsearch             fast         nf   0.851124  0.920260      0.729764
5  vsearch             size         nf   0.851122  0.920260      0.729763
6  vsearch  smallmem_length         nf   0.851122  0.920260      0.729763
7  vsearch    smallmem_size         nf   0.851122  0.920260      0.729763
1  usearch        fast_size         nf   0.843418  0.912246      0.718909
2  usearch  smallmem_length         nf   0.842845  0.913496      0.718144
3  usearch    smallmem_size         nf   0.842845  0.913496      0.718144

VSEARCH options makes no difference. For USEARCH, length-sorted slightly better. Minor differences between normal / fast and smallmem versions.

`USEARCH` pick: `fast_length` = `-cluster_fast -sort length
`

`VSEARCH` pick: `size` = `--cluster_size`

**Average clustering quality**

Rank by adjusted Rand index (per data set):

In [19]:
for (d, t), grp in df_joined_mean_avg.groupby(by = ['data_set', 'tool']):
    print('Data set: %s / Tool: %s' % (d, t))
    display(grp.sort_values(by = 'adjrandindex', ascending = False))

Data set: HC_V3-V4 / Tool: usearch


data_set       gt     tool             mode refinement  precision  \
0  HC_V3-V4  franzen  usearch      fast_length         nf   0.643079   
2  HC_V3-V4  franzen  usearch  smallmem_length         nf   0.637531   
3  HC_V3-V4  franzen  usearch    smallmem_size         nf   0.637531   
1  HC_V3-V4  franzen  usearch        fast_size         nf   0.639750   

     recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
0  0.844202      0.409204               9958.0      9958.0       1434.93   
2  0.854703      0.406743               9958.0      9958.0       1350.42   
3  0.854703      0.406743               9958.0      9958.0       1350.42   
1  0.847558      0.403198               9958.0      9958.0       1411.98   

   num_output_amplicons  output_mass  ds     rt  
0                9952.4       9958.0  HC  V3-V4  
2                9952.4       9958.0  HC  V3-V4  
3                9952.4       9958.0  HC  V3-V4  
1                9952.4       9958.0  HC  V3-V4

Data set: HC_V3-V4 / Tool: vsearch


data_set       gt     tool             mode refinement  precision  \
4  HC_V3-V4  franzen  vsearch             fast         nf   0.643781   
5  HC_V3-V4  franzen  vsearch             size         nf   0.643685   
6  HC_V3-V4  franzen  vsearch  smallmem_length         nf   0.643685   
7  HC_V3-V4  franzen  vsearch    smallmem_size         nf   0.643685   

     recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
4  0.868622      0.417428               9958.0      9958.0       1341.19   
5  0.868548      0.417372               9958.0      9958.0       1340.79   
6  0.868548      0.417372               9958.0      9958.0       1340.79   
7  0.868548      0.417372               9958.0      9958.0       1340.79   

   num_output_amplicons  output_mass  ds     rt  
4                9952.4       9958.0  HC  V3-V4  
5                9952.4       9958.0  HC  V3-V4  
6                9952.4       9958.0  HC  V3-V4  
7                9952.4       9958.0  HC  V3-V4

Data set: HC_V4 / Tool: usearch


...

data_set       gt     tool             mode refinement  precision  \
36  MC_V3-V4  franzen  vsearch             fast         nf   0.725665   
37  MC_V3-V4  franzen  vsearch             size         nf   0.725655   
38  MC_V3-V4  franzen  vsearch  smallmem_length         nf   0.725655   
39  MC_V3-V4  franzen  vsearch    smallmem_size         nf   0.725655   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
36  0.872111      0.553586               4966.0      4966.0        692.74   
37  0.872067      0.553544               4966.0      4966.0        692.77   
38  0.872067      0.553544               4966.0      4966.0        692.77   
39  0.872067      0.553544               4966.0      4966.0        692.77   

    num_output_amplicons  output_mass  ds     rt  
36                4962.6       4966.0  MC  V3-V4  
37                4962.6       4966.0  MC  V3-V4  
38                4962.6       4966.0  MC  V3-V4  
39                4962.6       4966.0  MC  V3-V4

Data set: MC_V4 / Tool: usearch


data_set       gt     tool             mode refinement  precision  \
40    MC_V4  franzen  usearch      fast_length         nf   0.638981   
42    MC_V4  franzen  usearch  smallmem_length         nf   0.597981   
43    MC_V4  franzen  usearch    smallmem_size         nf   0.597981   
41    MC_V4  franzen  usearch        fast_size         nf   0.598479   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
40  0.938934      0.540493               4966.0      4966.0        301.29   
42  0.964818      0.514676               4966.0      4966.0        205.25   
43  0.964818      0.514676               4966.0      4966.0        205.25   
41  0.963930      0.514325               4966.0      4966.0        206.12   

    num_output_amplicons  output_mass  ds  rt  
40                4101.5       4966.0  MC  V4  
42                4101.5       4966.0  MC  V4  
43                4101.5       4966.0  MC  V4  
41                4101.5       4966.0  MC  V4

Data set: MC_V4 / Tool: vsearch


data_set       gt     tool             mode refinement  precision  \
44    MC_V4  franzen  vsearch             fast         nf   0.597457   
45    MC_V4  franzen  vsearch             size         nf   0.597378   
46    MC_V4  franzen  vsearch  smallmem_length         nf   0.597378   
47    MC_V4  franzen  vsearch    smallmem_size         nf   0.597378   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
44  0.966312      0.515035               4966.0      4966.0        203.77   
45  0.966332      0.514919               4966.0      4966.0        203.75   
46  0.966332      0.514919               4966.0      4966.0        203.75   
47  0.966332      0.514919               4966.0      4966.0        203.75   

    num_output_amplicons  output_mass  ds  rt  
44                4101.5       4966.0  MC  V4  
45                4101.5       4966.0  MC  V4  
46                4101.5       4966.0  MC  V4  
47                4101.5       4966.0  MC  V4

Same tendencies as maximum.

Average the mean values over all data sets and sort by adjusted Rand index.

In [20]:
rows = []
for (t, m, f), grp in df_joined_mean_avg.groupby(by = ['tool', 'mode', 'refinement']):
    rows.append([t, m, f, grp['precision'].mean(), grp['recall'].mean(), grp['adjrandindex'].mean()])
pd.DataFrame(rows, columns = ['tool', 'mode', 'refinement', 'precision', 'recall', 'adjrandindex']).sort_values(by = 'adjrandindex', ascending = False)

tool             mode refinement  precision    recall  adjrandindex
0  usearch      fast_length         nf   0.683534  0.897564      0.536915
4  vsearch             fast         nf   0.663464  0.919245      0.529283
5  vsearch             size         nf   0.663415  0.919221      0.529237
6  vsearch  smallmem_length         nf   0.663415  0.919221      0.529237
7  vsearch    smallmem_size         nf   0.663415  0.919221      0.529237
2  usearch  smallmem_length         nf   0.661945  0.913719      0.524996
3  usearch    smallmem_size         nf   0.661945  0.913719      0.524996
1  usearch        fast_size         nf   0.663488  0.911192      0.524693

**N-best average clustering quality**

Rank by adjusted Rand index (per data set):

In [21]:
for (d, t), grp in df_joined_nbest_avg.groupby(by = ['data_set', 'tool']):
    print('Data set: %s / Tool: %s' % (d, t))
    display(grp.sort_values(by = 'adjrandindex', ascending = False))

Data set: HC_V3-V4 / Tool: usearch


data_set       gt     tool             mode refinement  precision  \
0  HC_V3-V4  franzen  usearch      fast_length         nf   0.727073   
2  HC_V3-V4  franzen  usearch  smallmem_length         nf   0.721751   
3  HC_V3-V4  franzen  usearch    smallmem_size         nf   0.721751   
1  HC_V3-V4  franzen  usearch        fast_size         nf   0.723113   

     recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
0  0.875593      0.530104               9958.0      9958.0        994.70   
2  0.887509      0.523642               9958.0      9958.0        912.02   
3  0.887509      0.523642               9958.0      9958.0        912.02   
1  0.879085      0.518181               9958.0      9958.0        974.32   

   num_output_amplicons  output_mass  ds     rt  
0                9952.4       9958.0  HC  V3-V4  
2                9952.4       9958.0  HC  V3-V4  
3                9952.4       9958.0  HC  V3-V4  
1                9952.4       9958.0  HC  V3-V4

Data set: HC_V3-V4 / Tool: vsearch


data_set       gt     tool             mode refinement  precision  \
4  HC_V3-V4  franzen  vsearch             fast         nf   0.737256   
5  HC_V3-V4  franzen  vsearch             size         nf   0.737155   
6  HC_V3-V4  franzen  vsearch  smallmem_length         nf   0.737155   
7  HC_V3-V4  franzen  vsearch    smallmem_size         nf   0.737155   

     recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
4  0.905547      0.544724               9958.0      9958.0        908.36   
5  0.905428      0.544618               9958.0      9958.0        907.94   
6  0.905428      0.544618               9958.0      9958.0        907.94   
7  0.905428      0.544618               9958.0      9958.0        907.94   

   num_output_amplicons  output_mass  ds     rt  
4                9952.4       9958.0  HC  V3-V4  
5                9952.4       9958.0  HC  V3-V4  
6                9952.4       9958.0  HC  V3-V4  
7                9952.4       9958.0  HC  V3-V4

Data set: HC_V4 / Tool: usearch


...

data_set       gt     tool             mode refinement  precision  \
36  MC_V3-V4  franzen  vsearch             fast         nf   0.806653   
37  MC_V3-V4  franzen  vsearch             size         nf   0.806641   
38  MC_V3-V4  franzen  vsearch  smallmem_length         nf   0.806641   
39  MC_V3-V4  franzen  vsearch    smallmem_size         nf   0.806641   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
36  0.917768      0.685002               4966.0      4966.0        447.20   
37  0.917703      0.684954               4966.0      4966.0        447.18   
38  0.917703      0.684954               4966.0      4966.0        447.18   
39  0.917703      0.684954               4966.0      4966.0        447.18   

    num_output_amplicons  output_mass  ds     rt  
36                4962.6       4966.0  MC  V3-V4  
37                4962.6       4966.0  MC  V3-V4  
38                4962.6       4966.0  MC  V3-V4  
39                4962.6       4966.0  MC  V3-V4

Data set: MC_V4 / Tool: usearch


data_set       gt     tool             mode refinement  precision  \
40    MC_V4  franzen  usearch      fast_length         nf   0.773033   
41    MC_V4  franzen  usearch        fast_size         nf   0.728843   
42    MC_V4  franzen  usearch  smallmem_length         nf   0.728389   
43    MC_V4  franzen  usearch    smallmem_size         nf   0.728389   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
40  0.908540      0.645536               4966.0      4966.0        452.58   
41  0.953799      0.629817               4966.0      4966.0        296.24   
42  0.954215      0.629736               4966.0      4966.0        294.76   
43  0.954215      0.629736               4966.0      4966.0        294.76   

    num_output_amplicons  output_mass  ds  rt  
40                4101.5       4966.0  MC  V4  
41                4101.5       4966.0  MC  V4  
42                4101.5       4966.0  MC  V4  
43                4101.5       4966.0  MC  V4

Data set: MC_V4 / Tool: vsearch


data_set       gt     tool             mode refinement  precision  \
44    MC_V4  franzen  vsearch             fast         nf   0.736342   
45    MC_V4  franzen  vsearch             size         nf   0.736342   
46    MC_V4  franzen  vsearch  smallmem_length         nf   0.736342   
47    MC_V4  franzen  vsearch    smallmem_size         nf   0.736342   

      recall  adjrandindex  num_input_amplicons  input_mass  num_clusters  \
44  0.955908      0.637638               4966.0      4966.0        294.88   
45  0.955908      0.637638               4966.0      4966.0        294.88   
46  0.955908      0.637638               4966.0      4966.0        294.88   
47  0.955908      0.637638               4966.0      4966.0        294.88   

    num_output_amplicons  output_mass  ds  rt  
44                4101.5       4966.0  MC  V4  
45                4101.5       4966.0  MC  V4  
46                4101.5       4966.0  MC  V4  
47                4101.5       4966.0  MC  V4

Same tendencies as maximum.

Average the N-best values over all data sets and sort by adjusted Rand index.

In [22]:
rows = []
for (t, m, f), grp in df_joined_nbest_avg.groupby(by = ['tool', 'mode', 'refinement']):
    rows.append([t, m, f, grp['precision'].mean(), grp['recall'].mean(), grp['adjrandindex'].mean()])
pd.DataFrame(rows, columns = ['tool', 'mode', 'refinement', 'precision', 'recall', 'adjrandindex']).sort_values(by = 'adjrandindex', ascending = False)

tool             mode refinement  precision    recall  adjrandindex
0  usearch      fast_length         nf   0.767570  0.923321      0.647412
4  vsearch             fast         nf   0.758596  0.944633      0.645477
5  vsearch             size         nf   0.758572  0.944604      0.645451
6  vsearch  smallmem_length         nf   0.758572  0.944604      0.645451
7  vsearch    smallmem_size         nf   0.758572  0.944604      0.645451
1  usearch        fast_size         nf   0.751130  0.937284      0.635742
2  usearch  smallmem_length         nf   0.749490  0.939342      0.635002
3  usearch    smallmem_size         nf   0.749490  0.939342      0.635002

Same as maximum.